### 📚 __Introduction__

You've performed brilliantly in the TripleTen course and have been offered an internship in the analytics department at Showz, an event ticketing company. Your first task is to help optimize marketing expenses.

You have:

- server logs with data on Showz visits from January 2017 to December 2018;
- a file with orders from this period;
- marketing expense statistics.

What you will research:

- how customers use the service;
- when they start purchasing;
- how much money each customer brings to the company;
- when revenue covers the customer acquisition cost.

#### 🧾 __Data Dictionary__

1. The visits table (server logs with data about website visits):

    - Uid: Unique user identifier.
    - Device: User's device.
    - Start Ts: Session start date and time.
    - End Ts: Session end date and time.
    - Source Id: Identifier of the ad source the user is using.

All dates in this table are in YYYY-MM-DD format.

2. The orders table (data about orders):

    - Uid: Unique identifier of the user who placed an order.
    - Buy Ts: Date and time of the order. 
    - Revenue: Showz's revenue from the order.

3. The costs table (data about marketing expenses):

    - source_id: Ad source identifier.
    - dt: Date.
    - costs: Spending on this ad source on this day.

### ✅ __Actions to be performed__

__Step 1__. Access the data and prepare it for analysis

Store the visit, order, and expense data in variables. Optimize the data for analysis. Make sure each column contains the correct data type.
File paths:

data/raw/visits_log_us.csv Access the dataset   
data/raw/orders_log_us.csv Access the dataset   
data/raw/costs_us.csv Access the dataset   

__Step 2__. Create reports and calculate metrics

- Visits:
    1. How many people use it each day, week, and month?
    2. How many sessions are there per day? (A user can have more than one session.)
    3. How long is each session?
    4. How often do users return?

- Sales:
    1. When do people start buying? (In KPI analysis, we're generally interested in the time between registration and conversion—that is, when the user becomes a customer. For example, if registration and the first purchase occur on the same day, the user might fall into the 0d Conversion category. If the first purchase occurs the next day, it would be 1d Conversion. You can use any approach that allows you to compare conversions across different cohorts so you can determine which cohort or marketing channel is most effective.)
    2. How many orders do they make during a given time period?
    3. What is the average purchase size?
    4. How much money do they bring in? (LTV)

- Marketing:
    1. How much money was spent? (Total/by acquisition source/over time)
    2. What was the customer acquisition cost from each source?
    3. How cost-effective were the investments? (ROMI)

Plot charts to show how these metrics differ for various devices and ad sources and how they change over time.

__Step 3__. Write a conclusion: Advise marketing experts how much money to invest and where.

Which sources/platforms would you recommend? Justify your selection: Which metrics did you focus on? Why? What conclusions did you draw after finding the metric values?


### 💻 __1. Notebook Libraries and Customization__

In [1]:
from IPython.display import display, HTML
from matplotlib import pyplot as plt
import numpy as np
import pandas as pd
import plotly.express as px
import re
from scipy import stats as st
import seaborn as sns
from tqdm import tqdm

pd.set_option('display.max_rows', 25)  # display max 25 rows
pd.set_option('display.max_columns', 25)  # display max 10 columns
# show max 15 characters in each column
pd.set_option('display.max_colwidth', 50)
pd.set_option('display.width', 150)  # Display max 150 characters in cell

### 💻 __2. Functions__

In [2]:
# Function used to detect missing values ​​not treated as NAN due to the use of keep_defaukt_na=False
def missing_values_check(df):

    missing_values = ['', ' ', 'N/A', 'none', 'None',
                      'null', 'NULL', 'NaN', 'nan', 'NAN', 'nat', 'NaT']

    for column in df.columns:

        if df[column].isin(missing_values).any():

            display(HTML(
                f"> Null values ​​in column <i>'{column}'</i>: <b>{df[column].isin(missing_values).sum()}</b>"))

        else:

            display(
                HTML(f"> No null values ​​exist in column <i>'{column}'</i>"))
            
# Function used to assign pd.NA to missing values
def missing_values_replace(df):

    missing_values = ['', ' ', 'N/A', 'none', 'None',
                      'null', 'NULL', 'NaN', 'nan', 'NAN', 'nat', 'NaT']

    for column in df.columns:

        try:

            # (None, np.nan, pd.NA, pd.NaT)
            df[column] = df[column].apply(lambda x: pd.NA if pd.isna(x) else x)

            # (missing_values))
            df[column] = df[column].replace(missing_values, pd.NA)

        except Exception as e:

            display(
                HTML(f"> Column <i>'{column}'</i> could not be processed: {e}"))

    return df

### 🔁 __3. Data Loading__

In [3]:
df_costs = pd.read_csv('../data/raw/costs_us.csv', sep=',', header='infer', keep_default_na=False)
df_orders = pd.read_csv('../data/raw/orders_log_us.csv', sep=',', header='infer', keep_default_na=False)
df_visits = pd.read_csv('../data/raw/visits_log_us.csv', sep=',', header='infer', keep_default_na=False)

### 🧹 __4. Data Cleanup__

##### **4.1** Data Overview

In [4]:
# df_costs Overview
df_costs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2542 entries, 0 to 2541
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   source_id  2542 non-null   int64  
 1   dt         2542 non-null   object 
 2   costs      2542 non-null   float64
dtypes: float64(1), int64(1), object(1)
memory usage: 59.7+ KB


In [5]:
df_costs

source_id          dt  costs
0             1  2017-06-01  75.20
1             1  2017-06-02  62.25
2             1  2017-06-03  36.53
3             1  2017-06-04  55.00
4             1  2017-06-05  57.08
...         ...         ...    ...
2537         10  2018-05-27   9.92
2538         10  2018-05-28  21.26
2539         10  2018-05-29  11.32
2540         10  2018-05-30  33.15
2541         10  2018-05-31  17.60

[2542 rows x 3 columns]

In [6]:
# df_orders Overview
df_orders.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   Buy Ts   50415 non-null  object 
 1   Revenue  50415 non-null  float64
 2   Uid      50415 non-null  uint64 
dtypes: float64(1), object(1), uint64(1)
memory usage: 1.2+ MB


In [7]:
df_orders

Buy Ts  Revenue                   Uid
0      2017-06-01 00:10:00    17.00  10329302124590727494
1      2017-06-01 00:25:00     0.55  11627257723692907447
2      2017-06-01 00:27:00     0.37  17903680561304213844
3      2017-06-01 00:29:00     0.55  16109239769442553005
4      2017-06-01 07:58:00     0.37  14200605875248379450
...                    ...      ...                   ...
50410  2018-05-31 23:50:00     4.64  12296626599487328624
50411  2018-05-31 23:50:00     5.80  11369640365507475976
50412  2018-05-31 23:54:00     0.30   1786462140797698849
50413  2018-05-31 23:56:00     3.67   3993697860786194247
50414  2018-06-01 00:02:00     3.42     83872787173869366

[50415 rows x 3 columns]

In [8]:
# df_visits Overview
df_visits.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 359400 entries, 0 to 359399
Data columns (total 5 columns):
 #   Column     Non-Null Count   Dtype 
---  ------     --------------   ----- 
 0   Device     359400 non-null  object
 1   End Ts     359400 non-null  object
 2   Source Id  359400 non-null  int64 
 3   Start Ts   359400 non-null  object
 4   Uid        359400 non-null  uint64
dtypes: int64(1), object(3), uint64(1)
memory usage: 13.7+ MB


In [9]:
df_visits

Device               End Ts  Source Id             Start Ts                   Uid
0         touch  2017-12-20 17:38:00          4  2017-12-20 17:20:00  16879256277535980062
1       desktop  2018-02-19 17:21:00          2  2018-02-19 16:53:00    104060357244891740
2         touch  2017-07-01 01:54:00          5  2017-07-01 01:54:00   7459035603376831527
3       desktop  2018-05-20 11:23:00          9  2018-05-20 10:59:00  16174680259334210214
4       desktop  2017-12-27 14:06:00          3  2017-12-27 14:06:00   9969694820036681168
...         ...                  ...        ...                  ...                   ...
359395  desktop  2017-07-29 19:07:19          2  2017-07-29 19:07:00  18363291481961487539
359396    touch  2018-01-25 17:38:19          1  2018-01-25 17:38:00  18370831553019119586
359397  desktop  2018-03-03 10:12:19          4  2018-03-03 10:12:00  18387297585500748294
359398  desktop  2017-11-02 10:12:19          5  2017-11-02 10:12:00  18388616944624776485
359399    touch  2017-09-10 13:13:19          2  2017-09-10 13:13:00  18396128934054549559

[359400 rows x 5 columns]

##### **4.2** Standardization of column heading formats (Lower case, snake case)

In [10]:
df_orders.columns = df_orders.columns.str.strip().str.lower().str.replace(' ', '_').str.replace(r'[^\w]', '', regex=True)
df_orders.columns

Index(['buy_ts', 'revenue', 'uid'], dtype='object')

In [11]:
df_visits.columns = df_visits.columns.str.strip().str.lower().str.replace(' ', '_').str.replace(r'[^\w]', '', regex=True)
df_visits.columns

Index(['device', 'end_ts', 'source_id', 'start_ts', 'uid'], dtype='object')

##### **4.2** Explicit Duplicate Removal

In [12]:
display(HTML(f"> <b>df_costs</b> explicit duplicates: {df_costs.duplicated().sum()}"))

In [13]:
display(HTML(f"> <b>df_orders</b> explicit duplicates: {df_orders.duplicated().sum()}"))

In [14]:
display(HTML(f"> <b>df_visits</b> explicit duplicates: {df_visits.duplicated().sum()}"))

##### **4.3** Missing Value Analysis

In [15]:
missing_values_check(df_costs)

In [16]:
missing_values_check(df_orders)

In [17]:
missing_values_check(df_visits)

##### _4.3.1_ pd.NA for missing values

In [18]:
df_costs = missing_values_replace(df_costs)
df_costs

source_id          dt  costs
0             1  2017-06-01  75.20
1             1  2017-06-02  62.25
2             1  2017-06-03  36.53
3             1  2017-06-04  55.00
4             1  2017-06-05  57.08
...         ...         ...    ...
2537         10  2018-05-27   9.92
2538         10  2018-05-28  21.26
2539         10  2018-05-29  11.32
2540         10  2018-05-30  33.15
2541         10  2018-05-31  17.60

[2542 rows x 3 columns]

In [19]:
df_orders = missing_values_replace(df_orders)
df_orders

buy_ts  revenue                   uid
0      2017-06-01 00:10:00    17.00  10329302124590727494
1      2017-06-01 00:25:00     0.55  11627257723692907447
2      2017-06-01 00:27:00     0.37  17903680561304213844
3      2017-06-01 00:29:00     0.55  16109239769442553005
4      2017-06-01 07:58:00     0.37  14200605875248379450
...                    ...      ...                   ...
50410  2018-05-31 23:50:00     4.64  12296626599487328624
50411  2018-05-31 23:50:00     5.80  11369640365507475976
50412  2018-05-31 23:54:00     0.30   1786462140797698849
50413  2018-05-31 23:56:00     3.67   3993697860786194247
50414  2018-06-01 00:02:00     3.42     83872787173869366

[50415 rows x 3 columns]

In [20]:
df_visits = missing_values_replace(df_visits)
df_visits

device               end_ts  source_id             start_ts                   uid
0         touch  2017-12-20 17:38:00          4  2017-12-20 17:20:00  16879256277535980062
1       desktop  2018-02-19 17:21:00          2  2018-02-19 16:53:00    104060357244891740
2         touch  2017-07-01 01:54:00          5  2017-07-01 01:54:00   7459035603376831527
3       desktop  2018-05-20 11:23:00          9  2018-05-20 10:59:00  16174680259334210214
4       desktop  2017-12-27 14:06:00          3  2017-12-27 14:06:00   9969694820036681168
...         ...                  ...        ...                  ...                   ...
359395  desktop  2017-07-29 19:07:19          2  2017-07-29 19:07:00  18363291481961487539
359396    touch  2018-01-25 17:38:19          1  2018-01-25 17:38:00  18370831553019119586
359397  desktop  2018-03-03 10:12:19          4  2018-03-03 10:12:00  18387297585500748294
359398  desktop  2017-11-02 10:12:19          5  2017-11-02 10:12:00  18388616944624776485
359399    touch  2017-09-10 13:13:19          2  2017-09-10 13:13:00  18396128934054549559

[359400 rows x 5 columns]

##### **4.4** Casting Datatypes

In [21]:
df_costs['dt'] = pd.to_datetime(df_costs['dt'])
display(HTML(f"> df_costs column: <b>'dt'</b> data type: <i>{df_costs['dt'].dtypes}</i>"))
df_costs

source_id         dt  costs
0             1 2017-06-01  75.20
1             1 2017-06-02  62.25
2             1 2017-06-03  36.53
3             1 2017-06-04  55.00
4             1 2017-06-05  57.08
...         ...        ...    ...
2537         10 2018-05-27   9.92
2538         10 2018-05-28  21.26
2539         10 2018-05-29  11.32
2540         10 2018-05-30  33.15
2541         10 2018-05-31  17.60

[2542 rows x 3 columns]

In [22]:
df_orders['buy_ts'] = pd.to_datetime(df_orders['buy_ts'])
display(HTML(f"> df_orders column: <b>'buy_ts'</b> data type: <i>{df_orders['buy_ts'].dtypes}</i>"))
df_orders

buy_ts  revenue                   uid
0     2017-06-01 00:10:00    17.00  10329302124590727494
1     2017-06-01 00:25:00     0.55  11627257723692907447
2     2017-06-01 00:27:00     0.37  17903680561304213844
3     2017-06-01 00:29:00     0.55  16109239769442553005
4     2017-06-01 07:58:00     0.37  14200605875248379450
...                   ...      ...                   ...
50410 2018-05-31 23:50:00     4.64  12296626599487328624
50411 2018-05-31 23:50:00     5.80  11369640365507475976
50412 2018-05-31 23:54:00     0.30   1786462140797698849
50413 2018-05-31 23:56:00     3.67   3993697860786194247
50414 2018-06-01 00:02:00     3.42     83872787173869366

[50415 rows x 3 columns]

In [23]:
df_visits['device'] = pd.Categorical(df_visits['device'])
df_visits['start_ts'] = pd.to_datetime(df_visits['start_ts'])
df_visits['end_ts'] = pd.to_datetime(df_visits['end_ts'])
display(HTML(f"> df_visits column: <b>'device'</b> data type: <i>{df_visits['device'].dtypes}</i>"))
display(HTML(f"> df_visits column: <b>'start_ts'</b> data type: <i>{df_visits['start_ts'].dtypes}</i>"))
display(HTML(f"> df_visits column: <b>'end_ts'</b> data type: <i>{df_visits['end_ts'].dtypes}</i>"))
df_visits

device              end_ts  source_id            start_ts                   uid
0         touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00  16879256277535980062
1       desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00    104060357244891740
2         touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   7459035603376831527
3       desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00  16174680259334210214
4       desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   9969694820036681168
...         ...                 ...        ...                 ...                   ...
359395  desktop 2017-07-29 19:07:19          2 2017-07-29 19:07:00  18363291481961487539
359396    touch 2018-01-25 17:38:19          1 2018-01-25 17:38:00  18370831553019119586
359397  desktop 2018-03-03 10:12:19          4 2018-03-03 10:12:00  18387297585500748294
359398  desktop 2017-11-02 10:12:19          5 2017-11-02 10:12:00  18388616944624776485
359399    touch 2017-09-10 13:13:19          2 2017-09-10 13:13:00  18396128934054549559

[359400 rows x 5 columns]

### 🧮 __5. Reports and Metrics__

##### **5.1** Visits

##### _5.1.1_ How many people use it every day, week and month?

In [24]:
# Get Day from 'start_ts'
df_visits_time_frame = df_visits.copy()
df_visits_time_frame['day'] = df_visits_time_frame['start_ts'].dt.day
df_visits_time_frame

device              end_ts  source_id            start_ts                   uid  day
0         touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00  16879256277535980062   20
1       desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00    104060357244891740   19
2         touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   7459035603376831527    1
3       desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00  16174680259334210214   20
4       desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   9969694820036681168   27
...         ...                 ...        ...                 ...                   ...  ...
359395  desktop 2017-07-29 19:07:19          2 2017-07-29 19:07:00  18363291481961487539   29
359396    touch 2018-01-25 17:38:19          1 2018-01-25 17:38:00  18370831553019119586   25
359397  desktop 2018-03-03 10:12:19          4 2018-03-03 10:12:00  18387297585500748294    3
359398  desktop 2017-11-02 10:12:19          5 2017-11-02 10:12:00  18388616944624776485    2
359399    touch 2017-09-10 13:13:19          2 2017-09-10 13:13:00  18396128934054549559   10

[359400 rows x 6 columns]

In [25]:
# Get Number of week from 'start_ts'
df_visits_time_frame['week'] = df_visits_time_frame['start_ts'].dt.isocalendar().week
df_visits_time_frame

device              end_ts  source_id            start_ts                   uid  day  week
0         touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00  16879256277535980062   20    51
1       desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00    104060357244891740   19     8
2         touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   7459035603376831527    1    26
3       desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00  16174680259334210214   20    20
4       desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   9969694820036681168   27    52
...         ...                 ...        ...                 ...                   ...  ...   ...
359395  desktop 2017-07-29 19:07:19          2 2017-07-29 19:07:00  18363291481961487539   29    30
359396    touch 2018-01-25 17:38:19          1 2018-01-25 17:38:00  18370831553019119586   25     4
359397  desktop 2018-03-03 10:12:19          4 2018-03-03 10:12:00  18387297585500748294    3     9
359398  desktop 2017-11-02 10:12:19          5 2017-11-02 10:12:00  18388616944624776485    2    44
359399    touch 2017-09-10 13:13:19          2 2017-09-10 13:13:00  18396128934054549559   10    36

[359400 rows x 7 columns]

In [26]:
# Get Month from 'start_ts'
df_visits_time_frame['month'] = df_visits_time_frame['start_ts'].dt.month
df_visits_time_frame

device              end_ts  source_id            start_ts                   uid  day  week  month
0         touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00  16879256277535980062   20    51     12
1       desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00    104060357244891740   19     8      2
2         touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   7459035603376831527    1    26      7
3       desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00  16174680259334210214   20    20      5
4       desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   9969694820036681168   27    52     12
...         ...                 ...        ...                 ...                   ...  ...   ...    ...
359395  desktop 2017-07-29 19:07:19          2 2017-07-29 19:07:00  18363291481961487539   29    30      7
359396    touch 2018-01-25 17:38:19          1 2018-01-25 17:38:00  18370831553019119586   25     4      1
359397  desktop 2018-03-03 10:12:19          4 2018-03-03 10:12:00  18387297585500748294    3     9      3
359398  desktop 2017-11-02 10:12:19          5 2017-11-02 10:12:00  18388616944624776485    2    44     11
359399    touch 2017-09-10 13:13:19          2 2017-09-10 13:13:00  18396128934054549559   10    36      9

[359400 rows x 8 columns]

In [27]:
# Get Year from 'start_ts'
df_visits_time_frame['year'] = df_visits_time_frame['start_ts'].dt.isocalendar().year
df_visits_time_frame

device              end_ts  source_id            start_ts                   uid  day  week  month  year
0         touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00  16879256277535980062   20    51     12  2017
1       desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00    104060357244891740   19     8      2  2018
2         touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   7459035603376831527    1    26      7  2017
3       desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00  16174680259334210214   20    20      5  2018
4       desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   9969694820036681168   27    52     12  2017
...         ...                 ...        ...                 ...                   ...  ...   ...    ...   ...
359395  desktop 2017-07-29 19:07:19          2 2017-07-29 19:07:00  18363291481961487539   29    30      7  2017
359396    touch 2018-01-25 17:38:19          1 2018-01-25 17:38:00  18370831553019119586   25     4      1  2018
359397  desktop 2018-03-03 10:12:19          4 2018-03-03 10:12:00  18387297585500748294    3     9      3  2018
359398  desktop 2017-11-02 10:12:19          5 2017-11-02 10:12:00  18388616944624776485    2    44     11  2017
359399    touch 2017-09-10 13:13:19          2 2017-09-10 13:13:00  18396128934054549559   10    36      9  2017

[359400 rows x 9 columns]

In [28]:
# Visits per day (DAU)
df_visits_time_frame_day = df_visits_time_frame.groupby(['year', 'month', 'day'])['uid'].nunique().reset_index()
df_visits_time_frame_day.columns = ['year', 'month', 'day', 'visits_per_day']
df_visits_time_frame_day['date'] = pd.to_datetime(df_visits_time_frame_day['year'].astype(str) + '-' + 
                                                  df_visits_time_frame_day['month'].astype(str) + '-' +
                                                  df_visits_time_frame_day['day'].astype(str)).dt.date
df_visits_time_frame_day

year  month  day  visits_per_day        date
0    2017      6    1             605  2017-06-01
1    2017      6    2             608  2017-06-02
2    2017      6    3             445  2017-06-03
3    2017      6    4             476  2017-06-04
4    2017      6    5             820  2017-06-05
..    ...    ...  ...             ...         ...
359  2018      5   27             620  2018-05-27
360  2018      5   28            1039  2018-05-28
361  2018      5   29             948  2018-05-29
362  2018      5   30            1289  2018-05-30
363  2018      5   31            1997  2018-05-31

[364 rows x 5 columns]

In [29]:
fig = px.line(df_visits_time_frame_day, x="date", y="visits_per_day", markers=True)
fig.update_traces(marker=dict(symbol="circle-dot", size=5))
fig.update_xaxes(dtick="M1", # tickformat="%b",
                 ticklabelmode="period")
fig.update_layout(title='Daily Active Users (DAU)', xaxis_title="Date (Day-Month-Year)", yaxis_title="Visits per Day")
fig.show()

In [30]:
# Visits per week (WAU)
df_visits_time_frame_week = df_visits_time_frame.groupby(['year', 'week'])['uid'].nunique().reset_index()
df_visits_time_frame_week.columns = ['year', 'week', 'visits_per_week']
df_visits_time_frame_week['date'] = pd.to_datetime(df_visits_time_frame_week['year'].astype(str) + 
                                                   df_visits_time_frame_week['week'].astype(str) + "1",
                                                  format="%Y%W%w")
df_visits_time_frame_week

year  week  visits_per_week       date
0   2017    22             2021 2017-05-29
1   2017    23             4129 2017-06-05
2   2017    24             2812 2017-06-12
3   2017    25             2878 2017-06-19
4   2017    26             3064 2017-06-26
..   ...   ...              ...        ...
48  2018    18             3916 2018-04-30
49  2018    19             4128 2018-05-07
50  2018    20             5070 2018-05-14
51  2018    21             4995 2018-05-21
52  2018    22             4892 2018-05-28

[53 rows x 4 columns]

In [31]:
fig = px.line(df_visits_time_frame_week, x="date", y="visits_per_week", markers=True)
fig.update_traces(marker=dict(symbol="circle-dot", size=5))
fig.update_xaxes(dtick=604800000, tickformat="%Y-%m-%d", ticklabelmode="period")
fig.update_layout(title='Weekly Active Users (WAU)', xaxis_title="Date (first day of the week)", yaxis_title="Visits per week")
fig.show()

In [32]:
# Visits per month (MAU)
df_visits_time_frame_month = df_visits_time_frame.groupby(['year', 'month'])['uid'].nunique().reset_index()
df_visits_time_frame_month.columns = ['year', 'month', 'visits_per_month']
df_visits_time_frame_month['date'] = pd.to_datetime(df_visits_time_frame_month['year'].astype(str) + '-' + 
                                                  df_visits_time_frame_month['month'].astype(str))
df_visits_time_frame_month

year  month  visits_per_month       date
0   2017      6             13259 2017-06-01
1   2017      7             14183 2017-07-01
2   2017      8             11631 2017-08-01
3   2017      9             18975 2017-09-01
4   2017     10             29692 2017-10-01
5   2017     11             32797 2017-11-01
6   2017     12             31557 2017-12-01
7   2018      1             28716 2018-01-01
8   2018      2             28749 2018-02-01
9   2018      3             27473 2018-03-01
10  2018      4             21008 2018-04-01
11  2018      5             20701 2018-05-01

In [33]:
fig = px.line(df_visits_time_frame_month, x="date", y="visits_per_month", markers=True)
fig.update_traces(marker=dict(symbol="circle-dot", size=5))
fig.update_xaxes(dtick="M1", # tickformat="%b",
                 ticklabelmode="period")
fig.update_layout(title='Monthly Active Users (MAU)', xaxis_title="Date (Month-Year)", yaxis_title="Visits per Month")
fig.show()

##### _5.1.2_ How many sessions are there per day? (A user can have more than one session)

In [34]:
df_visits_time_frame_sessions = df_visits_time_frame.copy()
df_visits_time_frame_sessions = df_visits_time_frame_sessions.drop(labels=['day', 'week', 'month', 'year'], axis=1)
df_visits_time_frame_sessions['date'] = df_visits_time_frame_sessions['start_ts'].dt.date
df_visits_time_frame_sessions

device              end_ts  source_id            start_ts                   uid        date
0         touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00  16879256277535980062  2017-12-20
1       desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00    104060357244891740  2018-02-19
2         touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   7459035603376831527  2017-07-01
3       desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00  16174680259334210214  2018-05-20
4       desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   9969694820036681168  2017-12-27
...         ...                 ...        ...                 ...                   ...         ...
359395  desktop 2017-07-29 19:07:19          2 2017-07-29 19:07:00  18363291481961487539  2017-07-29
359396    touch 2018-01-25 17:38:19          1 2018-01-25 17:38:00  18370831553019119586  2018-01-25
359397  desktop 2018-03-03 10:12:19          4 2018-03-03 10:12:00  18387297585500748294  2018-03-03
359398  desktop 2017-11-02 10:12:19          5 2017-11-02 10:12:00  18388616944624776485  2017-11-02
359399    touch 2017-09-10 13:13:19          2 2017-09-10 13:13:00  18396128934054549559  2017-09-10

[359400 rows x 6 columns]

In [35]:
df_visits_time_frame_sessions = df_visits_time_frame_sessions.groupby('date')['uid'].count().reset_index(name='sessions')
df_visits_time_frame_sessions

date  sessions
0    2017-06-01       664
1    2017-06-02       658
2    2017-06-03       477
3    2017-06-04       510
4    2017-06-05       893
..          ...       ...
359  2018-05-27       672
360  2018-05-28      1156
361  2018-05-29      1035
362  2018-05-30      1410
363  2018-05-31      2256

[364 rows x 2 columns]

In [36]:
fig = px.line(df_visits_time_frame_sessions, x="date", y="sessions", markers=True)
fig.update_traces(marker=dict(symbol="circle-dot", size=5))
fig.update_xaxes(dtick="M1", # tickformat="%b",
                 ticklabelmode="period")
fig.update_layout(title='Sessions per Day', xaxis_title="Date", yaxis_title="Sessions per Day")
fig.show()

In [37]:
# Make sure DAU is different from Sessions
df_compare = df_visits_time_frame_day.merge(df_visits_time_frame_sessions, on=['date'])
df_compare = df_compare.drop(labels=['year', 'month', 'day'], axis=1)
df_compare

visits_per_day        date  sessions
0               605  2017-06-01       664
1               608  2017-06-02       658
2               445  2017-06-03       477
3               476  2017-06-04       510
4               820  2017-06-05       893
..              ...         ...       ...
359             620  2018-05-27       672
360            1039  2018-05-28      1156
361             948  2018-05-29      1035
362            1289  2018-05-30      1410
363            1997  2018-05-31      2256

[364 rows x 3 columns]

In [38]:
fig = px.line(df_compare, x="date", y=["visits_per_day", "sessions"], labels={"value": "Count", "variable": "Metric", "date": "Date" },
              title="Sessions per Day vs Daily Active Users (DAU)")

fig.show()

In [39]:
df_compare.columns = ['n_users', 'date', 'n_sessions']
df_compare['sessions_per_user'] = (df_compare['n_sessions'] / df_compare['n_users'])
df_compare

n_users        date  n_sessions  sessions_per_user
0        605  2017-06-01         664           1.097521
1        608  2017-06-02         658           1.082237
2        445  2017-06-03         477           1.071910
3        476  2017-06-04         510           1.071429
4        820  2017-06-05         893           1.089024
..       ...         ...         ...                ...
359      620  2018-05-27         672           1.083871
360     1039  2018-05-28        1156           1.112608
361      948  2018-05-29        1035           1.091772
362     1289  2018-05-30        1410           1.093871
363     1997  2018-05-31        2256           1.129695

[364 rows x 4 columns]

##### _5.1.3_ How long does each session last?

In [ ]:
# Session duration
df_visits_time_frame['session_duration'] = (df_visits_time_frame['end_ts'] - df_visits_time_frame['start_ts']).dt.total_seconds() / 60
df_visits_time_frame

device              end_ts  source_id            start_ts                   uid  day  week  month  year  session_duration
0         touch 2017-12-20 17:38:00          4 2017-12-20 17:20:00  16879256277535980062   20    51     12  2017         18.000000
1       desktop 2018-02-19 17:21:00          2 2018-02-19 16:53:00    104060357244891740   19     8      2  2018         28.000000
2         touch 2017-07-01 01:54:00          5 2017-07-01 01:54:00   7459035603376831527    1    26      7  2017          0.000000
3       desktop 2018-05-20 11:23:00          9 2018-05-20 10:59:00  16174680259334210214   20    20      5  2018         24.000000
4       desktop 2017-12-27 14:06:00          3 2017-12-27 14:06:00   9969694820036681168   27    52     12  2017          0.000000
...         ...                 ...        ...                 ...                   ...  ...   ...    ...   ...               ...
359395  desktop 2017-07-29 19:07:19          2 2017-07-29 19:07:00  18363291481961487539   29    30      7  2017          0.316667
359396    touch 2018-01-25 17:38:19          1 2018-01-25 17:38:00  18370831553019119586   25     4      1  2018          0.316667
359397  desktop 2018-03-03 10:12:19          4 2018-03-03 10:12:00  18387297585500748294    3     9      3  2018          0.316667
359398  desktop 2017-11-02 10:12:19          5 2017-11-02 10:12:00  18388616944624776485    2    44     11  2017          0.316667
359399    touch 2017-09-10 13:13:19          2 2017-09-10 13:13:00  18396128934054549559   10    36      9  2017          0.316667

[359400 rows x 10 columns]

In [ ]:
# Plot without possible outliers, if available
p99 = df_visits_time_frame['session_duration'].quantile(0.99)
fig = px.histogram(df_visits_time_frame.query("session_duration <= @p99"), x="session_duration", nbins=120, title="Session Duration Distribution (≤99th pct)",
                   labels={"session_duration":"Session duration (min)"})
fig.update_layout(bargap=0.05)
fig.show()

In [56]:
display(HTML(f"> Average sesion duration (ASL): {df_visits_time_frame['session_duration'].mean():.3f} mins."))

##### _5.1.4_ How often do users return?

In [62]:
# Get sticky factors (daily, weekly, monthly)
sticky_wau = (df_visits_time_frame_day['visits_per_day'].mean() / df_visits_time_frame_week['visits_per_week'].mean()) * 100
sticky_mau = (df_visits_time_frame_day['visits_per_day'].mean() / df_visits_time_frame_month['visits_per_month'].mean()) * 100

display(HTML(f"> Weekly percentage of returning users: {sticky_wau:.3f}"))
display(HTML(f"> Monthly percentage of returning users: {sticky_mau:.3f}"))

##### **5.2** Sales

##### _5.2.1_ When do people start buying?   
(In KPI analysis, we're generally interested in the time between registration and conversion—that is, when a user becomes a customer. For example, if registration and the first purchase occur on the same day, the user might fall into the 0d Conversion category. If the first purchase occurs the next day, it would be 1d Conversion. You can use any approach that allows you to compare conversions across different cohorts to determine which cohort or marketing channel is most effective.)

##### _5.2.2_ How many orders do you make during a given period of time?

##### _5.2.3_ What is the average purchase size?

##### _5.2.4_ How much money do they bring? (LTV)

##### **5.3** Marketing